For inverted index created using positional information already built, perform a wild card query using permuterm index and K gram index.
For the 20 News groups dataset, write a word count program using Map reduce. Use collection frequency as another method.





## Inverted Index Creation

In [3]:
from nltk.tokenize import TweetTokenizer
import re
import nltk
import sys
import os
import sklearn
import time

In [9]:
nltk.download('stopwords')
from nltk.corpus import stopwords
stopWords=set(stopwords.words('english'))

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [4]:
from sklearn.datasets import fetch_20newsgroups
train = fetch_20newsgroups(subset='train')

### PREPROCESS THE DATA

In [11]:
# Cleaning the data - use regex 
for i in range(len(train.data)):
    train.data[i] = ' '.join(re.sub("(@[A-Za-z0-9]+)|([^0-9A-Za-z \t])|(\w+:\/\/\S+)"," ", train.data[i]).split())

# Do case folding 
for i in range(len(train.data)):
    train.data[i]=train.data[i].lower()

In [14]:
# REMOVE STOP WORDS

clean = []
for item in train.data:
  x = item.split()
  curr = []
  for j in x:
    if j not in stopWords:
      curr.append(j)
  clean.append(curr)

print(clean[0:5])

[['lerxst', 'umd', 'edu', 'thing', 'subject', 'car', 'nntp', 'posting', 'host', 'rac3', 'wam', 'umd', 'edu', 'organization', 'university', 'maryland', 'college', 'park', 'lines', '15', 'wondering', 'anyone', 'could', 'enlighten', 'car', 'saw', 'day', '2', 'door', 'sports', 'car', 'looked', 'late', '60s', 'early', '70s', 'called', 'bricklin', 'doors', 'really', 'small', 'addition', 'front', 'bumper', 'separate', 'rest', 'body', 'know', 'anyone', 'tellme', 'model', 'name', 'engine', 'specs', 'years', 'production', 'car', 'made', 'history', 'whatever', 'info', 'funky', 'looking', 'car', 'please', 'e', 'mail', 'thanks', 'il', 'brought', 'neighborhood', 'lerxst'], ['guykuo', 'u', 'washington', 'edu', 'guy', 'kuo', 'subject', 'si', 'clock', 'poll', 'final', 'call', 'summary', 'final', 'call', 'si', 'clock', 'reports', 'keywords', 'si', 'acceleration', 'clock', 'upgrade', 'article', 'shelley', '1qvfo9innc3s', 'organization', 'university', 'washington', 'lines', '11', 'nntp', 'posting', 'host'

In [44]:
import nltk
nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [45]:
lmtzr=WordNetLemmatizer()

In [46]:
temp=[]
l1 = len(clean)
for i in range(l1):
    l2=len(clean[i])
    temp1=[]
    for j in range(l2):
        temp1.append(lmtzr.lemmatize(clean[i][j]))
    temp.append(temp1)

In [47]:
temp

[['lerxst',
  'umd',
  'edu',
  'thing',
  'subject',
  'car',
  'nntp',
  'posting',
  'host',
  'rac3',
  'wam',
  'umd',
  'edu',
  'organization',
  'university',
  'maryland',
  'college',
  'park',
  'line',
  '15',
  'wondering',
  'anyone',
  'could',
  'enlighten',
  'car',
  'saw',
  'day',
  '2',
  'door',
  'sport',
  'car',
  'looked',
  'late',
  '60',
  'early',
  '70',
  'called',
  'bricklin',
  'door',
  'really',
  'small',
  'addition',
  'front',
  'bumper',
  'separate',
  'rest',
  'body',
  'know',
  'anyone',
  'tellme',
  'model',
  'name',
  'engine',
  'spec',
  'year',
  'production',
  'car',
  'made',
  'history',
  'whatever',
  'info',
  'funky',
  'looking',
  'car',
  'please',
  'e',
  'mail',
  'thanks',
  'il',
  'brought',
  'neighborhood',
  'lerxst'],
 ['guykuo',
  'u',
  'washington',
  'edu',
  'guy',
  'kuo',
  'subject',
  'si',
  'clock',
  'poll',
  'final',
  'call',
  'summary',
  'final',
  'call',
  'si',
  'clock',
  'report',
  'keyw

In [48]:
from nltk.stem import PorterStemmer
from nltk.tokenize import word_tokenize 

In [49]:
stemmer=PorterStemmer()  
temps=[]
for i in range(len(temp)):
    l2 = len(temp[i])
    temp1s=[]
    for j in range(l2):
        temp1s.append(stemmer.stem(temp[i][j]))
    temps.append(temp1s)

In [50]:
print(temps[0])

['lerxst', 'umd', 'edu', 'thing', 'subject', 'car', 'nntp', 'post', 'host', 'rac3', 'wam', 'umd', 'edu', 'organ', 'univers', 'maryland', 'colleg', 'park', 'line', '15', 'wonder', 'anyon', 'could', 'enlighten', 'car', 'saw', 'day', '2', 'door', 'sport', 'car', 'look', 'late', '60', 'earli', '70', 'call', 'bricklin', 'door', 'realli', 'small', 'addit', 'front', 'bumper', 'separ', 'rest', 'bodi', 'know', 'anyon', 'tellm', 'model', 'name', 'engin', 'spec', 'year', 'product', 'car', 'made', 'histori', 'whatev', 'info', 'funki', 'look', 'car', 'pleas', 'e', 'mail', 'thank', 'il', 'brought', 'neighborhood', 'lerxst']


### INVERTED INDEX CREATION

In [51]:
#Creating an inverted index
inv_idx=dict()
for i in range(len(temps)):
    curr_id=i
    for token in temps[i]:
        if token not in inv_idx.keys():
            inv_idx[token]=[]
        inv_idx[token].append(curr_id)

### MAP REDUCE

In [52]:
li=[]
for i in train.data:
    x=i.split()
    for j in x:
        li.append([j,1])

In [53]:
for i in li:
    i[0]=i[0].lower()

In [54]:
d={}
for i in li:
    if i[0] in d:
        d[i[0]]+=i[1]
    else:
        d[i[0]]=i[1]

In [55]:
map_reduce=[(i,d[i]) for i in d]

In [56]:
map_reduce

[('from', 22673),
 ('lerxst', 4),
 ('umd', 295),
 ('edu', 21319),
 ('where', 2716),
 ('s', 22493),
 ('my', 9738),
 ('thing', 1532),
 ('subject', 12265),
 ('what', 9863),
 ('car', 1312),
 ('is', 43495),
 ('this', 20123),
 ('nntp', 4809),
 ('posting', 5507),
 ('host', 4993),
 ('rac3', 7),
 ('wam', 35),
 ('organization', 11233),
 ('university', 5589),
 ('of', 69047),
 ('maryland', 127),
 ('college', 628),
 ('park', 223),
 ('lines', 11835),
 ('15', 1807),
 ('i', 53084),
 ('was', 13659),
 ('wondering', 306),
 ('if', 13646),
 ('anyone', 2468),
 ('out', 6217),
 ('there', 9690),
 ('could', 3511),
 ('enlighten', 27),
 ('me', 6809),
 ('on', 20502),
 ('saw', 550),
 ('the', 146690),
 ('other', 5189),
 ('day', 1474),
 ('it', 33637),
 ('a', 64244),
 ('2', 10364),
 ('door', 266),
 ('sports', 169),
 ('looked', 344),
 ('to', 75072),
 ('be', 19287),
 ('late', 296),
 ('60s', 19),
 ('early', 472),
 ('70s', 26),
 ('called', 1154),
 ('bricklin', 4),
 ('doors', 90),
 ('were', 5412),
 ('really', 2180),
 ('sma

In [57]:
li1=[]
for i in train.data:
    x=i.split()
    for j in x:
        li1.append(j.lower())

In [58]:
li1

['from',
 'lerxst',
 'umd',
 'edu',
 'where',
 's',
 'my',
 'thing',
 'subject',
 'what',
 'car',
 'is',
 'this',
 'nntp',
 'posting',
 'host',
 'rac3',
 'wam',
 'umd',
 'edu',
 'organization',
 'university',
 'of',
 'maryland',
 'college',
 'park',
 'lines',
 '15',
 'i',
 'was',
 'wondering',
 'if',
 'anyone',
 'out',
 'there',
 'could',
 'enlighten',
 'me',
 'on',
 'this',
 'car',
 'i',
 'saw',
 'the',
 'other',
 'day',
 'it',
 'was',
 'a',
 '2',
 'door',
 'sports',
 'car',
 'looked',
 'to',
 'be',
 'from',
 'the',
 'late',
 '60s',
 'early',
 '70s',
 'it',
 'was',
 'called',
 'a',
 'bricklin',
 'the',
 'doors',
 'were',
 'really',
 'small',
 'in',
 'addition',
 'the',
 'front',
 'bumper',
 'was',
 'separate',
 'from',
 'the',
 'rest',
 'of',
 'the',
 'body',
 'this',
 'is',
 'all',
 'i',
 'know',
 'if',
 'anyone',
 'can',
 'tellme',
 'a',
 'model',
 'name',
 'engine',
 'specs',
 'years',
 'of',
 'production',
 'where',
 'this',
 'car',
 'is',
 'made',
 'history',
 'or',
 'whatever',


### PERMUTERM INDEX

In [59]:
permuterm_index={}
for key in sorted(inv_idx.keys()):
  dkey=key+"$"
  for i in range(len(dkey),0,-1):
    k=dkey[i:] + dkey[:i]
    permuterm_index[k]=key

Permuterm Index Query

In [61]:
query = input('Enter Query : ')

parts = query.split("*")

if parts[1] == '':
    case = 1
elif parts[0] == '':
    case = 2
elif parts[0] != '' and parts[1] != '':
    case = 3

print("case = ", case)

def prefix_match(term, prefix):
    term_list = []
    for tk in term.keys():
        if tk.startswith(prefix):
            term_list.append(term[tk])
    return term_list

def processQuery(query):    
    term_list = prefix_match(permuterm_index,query)
    print(term_list)

if case == 1:
    query = parts[0]
elif case == 2:
    query = parts[1] + "$"
elif case == 3:
    query = parts[1] + "$" + parts[0]
elif case == 4:
    queryA = parts[2] + "$" + parts[0]
    queryB = parts[1]

processQuery(query)

Enter Query : he*
case =  1
['04he', '118jheoyo', '12bhe', '1p7hez', '3he', '4he', '4jdjnhe', '5l4he', '5phe1', '5porsche356sc', '6q04he', '73vwporsche914', '7helx', '7hem', '7heo', '8he227', '8hefj', '8j4the', 'aachen', 'acetominophen', 'acheamenid', 'acheiv', 'acheng', 'achevia', 'adher', 'adhes', 'adhess', 'adshead', 'aesthet', 'aether', 'afhetzel', 'ahead', 'aheada', 'ahem', 'ahemmm', 'aherskow', 'ahithophel', 'airhead', 'alanchem', 'alchemi', 'alchemist', 'allegheni', 'altheim', 'altheimm', 'amherst', 'amphenol', 'amphetamin', 'anaesthesi', 'anaesthesiologi', 'anaheim', 'anasthesia', 'anathema', 'anesthesia', 'anesthesiolog', 'anesthet', 'anhedon', 'anheus', 'anthem', 'antiochen', 'antithesi', 'antithet', 'anywher', 'apartheid', 'apatheist', 'apathet', 'aphelion', 'apotheosi', 'applicationshel', 'applicationshellwidgetclass', 'apprehend', 'apprehens', 'apshel', 'archeitectur', 'archeolog', 'archeologist', 'archer', 'archeri', 'archetyp', 'arimathea', 'arishem', 'armenischen', 'arr

# K-gram index

In [62]:
wildcard = input('Enter Query: ')

grams = []
k = 3

if "*" not in wildcard[:k-1]:
    grams.append(wildcard[:k-1])

for i in range(len(wildcard)-k+1):
    if "*" not in wildcard[i:i+k]:
        grams.append(wildcard[i:i+k])

if "*" not in wildcard[-k+1:]:
    grams.append(wildcard[-k+1:])
print('Different combinations: ',grams)

Enter Query: stay
Different combinations:  ['st', 'sta', 'tay', 'ay']


Matching terms for different combinations

In [63]:
gdict = dict()
for i in grams:
    gdict[i] = set()
    for j in inv_idx:
        if i in j:
            gdict[i].add(j)
for i in gdict.keys():
    print(i, ":", gdict[i])

st : {'testprogram', 'allergist', 'straigten', 'samenstel', 'moster', 'fireston', 'idlastro', 'abstinencn', 'st157a', 'australopithecu', 'stockfisch', 'astound', 'statler', 'ystl', 'stcarm', 'tachistoscop', 'conestoga', 'fairest', 'statewid', '2stroke', 'xmustandardcolormap', 'aston', 'stagehand', 'wittgenstein', 'stutter', 'pistol', 'valvestem', 'contest', 'steinbron', 'mustenid', 'fmgst', 'stevep', 'st1401a', 'hostag', 'staf', 'acurist', 'stif', 'sistema', 'rstfd0mjn', 'thester', 'mainstay', 'dsto', 'xtdisplaystringconversionwarn', 'nonsteroid', 'akerstrom', 'westwind', 'storyvil', '5st3p', 'stephanopol', 'uderstand', 'messiest', 'phototransistor', 'aesthet', 'nassestr', 'ultrastor', 'stagnant', 'stong', 'stimulu', 'dusti', 'stettina', 'staal', 'qst3qs13p', 'stilgar', 'stressor', 'fontlist', 'east', 'celest', 'destruct', 'dwestner', 'antitrust', 'eostarum', 'universalist', 'arabist', 'plutoniumsurveillanceterroristciaassassinationirancontrawirefraudcryptolog', 'chast', 'westborough',

In [64]:
import functools

In [65]:
terms = list(functools.reduce(lambda x, y: x & y, list(gdict.values())))
print('Matched Terms: ')
print(terms)

res = set()
for i in terms:
    for j in inv_idx[i]:
        res.add(j)
print('Matched DocIDs: ')
print(res)

Matched Terms: 
['stay', 'hyerstay', 'stayng', 'mainstay', 'stayin']
Matched DocIDs: 
{2050, 6147, 17, 2066, 33, 6178, 10281, 6204, 4158, 6229, 10332, 6238, 4195, 8292, 4200, 8299, 10347, 10354, 8312, 8314, 127, 4230, 136, 6280, 4234, 2188, 147, 8346, 4253, 10397, 8358, 170, 10430, 2242, 4291, 8387, 4300, 205, 2254, 4304, 2266, 2273, 4323, 10475, 4332, 4333, 2286, 254, 6403, 261, 2316, 6413, 8479, 10531, 6437, 2345, 6442, 2349, 8503, 4411, 322, 8514, 2385, 4443, 2396, 2397, 2407, 6505, 8579, 10637, 2453, 2464, 8619, 2476, 443, 4544, 452, 2502, 458, 8658, 2526, 6632, 10734, 8698, 2554, 4614, 4616, 10761, 10765, 8722, 8726, 10795, 10797, 2609, 573, 2622, 4681, 8782, 8783, 10836, 8789, 2648, 4709, 6762, 623, 8825, 10879, 644, 8836, 6792, 6814, 2719, 8862, 4770, 6819, 8874, 4783, 700, 706, 8906, 6859, 727, 6880, 4835, 10982, 6894, 4861, 11013, 6918, 775, 6922, 8979, 6933, 4886, 8984, 2847, 805, 2853, 11048, 6954, 2859, 6962, 11065, 11070, 836, 6985, 6987, 4953, 7007, 7012, 11113, 2944, 500